![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 12. <i>Key logging</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Badania nad komputerowym wspomaganiem tłumaczenia często prowadzone są przy użyciu metodologii testowania interfejsów użytkownika - UI/UX testing. Program typu CAT traktuje się wówczas jak każdy inny program komputerowy i przeprowadza testy wydajności i użyteczności.

Testy takie prowadzone są zawsze na użytkownikach końcowych, w tym przypadku - na tłumaczach. Podstawowym celem testów jest próba zaobserwowania faktycznego sposobu pracy tłumacza - które funkcje programu są przez niego wykorzystywane najczęściej, jakich innych narzędzi poza CAT-em używa on do swojej pracy, które funkcje programu działają zgodnie, a które niezgodnie z intuicją użytkownika oraz wiele innych czynników. Aby wszystkie te analizy były możliwe, konieczne jest zgromadzenie jak największej ilości danych dotyczących przebiegu testu.

Testy są przede wszystkim nagrywane. Nagrywany jest zarówno ekran komputera (screen capture), jak i sam użytkownik pracujący przy komputerze. To jednak nie wszystko - często stosuje się specjalne techniki eye-trackingu, które są w stanie określić, w który punk ekranu użytkownik aktualnie patrzy. Dane pozyskane w ten sposób używane są do analizy czasu znalezienia przez użytkownika potrzebnej mu funkcji oraz zidentyfikowania miejsc, gdzie tej funkcji poszukiwał. Można również wyznaczyć obszary ekranu, które często skupiają uwagę użytkownika. 

Dodatkowo stosuje się jeszcze jedną technikę, która jest szczególnie przydatna z punktu widzenia analizy procesu tłumaczenia. Wykonuje się pełny key logging, tj. zapisuje się każde uderzenie użytkownika w dowolny klawisz na klawiaturze wraz z precyzyjnym czasem tego uderzenia. Dane pozyskane w ten sposób pozwalają na przeprowadzenie szeregu interesujących analiz.

Zapoznajmy się najpierw z programem typu key logger:

`sudo pip3 install keyboard`

In [ ]:
import keyboard


def report_key(event):
    print(event)

keyboard.on_release(callback=report_key)
keyboard.wait()

UWAGA! Aby uruchomić powyższy kod na Linuxie konieczne są uprawnienia administratora (pytanie poza konkursem - dlaczego?)

### Ćwiczenie 1: Wykorzystując powyższy kod napisz keylogger, który zapisuje wszystkie uderzenia w klawisze do pliku. Format pliku jest dowolny, każdy wpis musi zawierać precyzyjną godzinę uderzenia oraz uderzony klawisz. Uruchom program i przepisz paragraf dowolnie wybranego tekstu.

Celem powyższego ćwiczenia jest pozyskanie danych testowych. Dalsze analizy będziemy prowadzili już bez key loggera, starając się korzystać jedynie z danych zapisanych w pliku. Oczywiście, jeśli zajdzie taka konieczność, można w każdej chwili wygenerować sobie nowy plik.

In [ ]:
import keyboard
from datetime import datetime

# Ścieżka do pliku, w którym będą zapisywane dane
log_file = "keylog.txt"

def report_key(event):
    with open(log_file, "a") as f:
        # Pobieramy aktualny czas
        timestamp = datetime.now().strftime('%Y-%m-%d %H:%M:%S.%f')
        # Zapisujemy czas i wciśnięty klawisz do pliku
        f.write(f"{timestamp} - {event.name}\n")

# Ustawienie callbacka dla zdarzeń klawiatury
keyboard.on_release(callback=report_key)

# Czekanie na zdarzenia klawiatury
keyboard.wait()


### Ćwiczenie 2: Napisz program, który wyliczy średnią prędkość pisania. Wykryj, kiedy użytkownik zaczął pisać. Nie bierz pod uwagę przerw dłuższych niż 5 sekund. Podaj prędkość pisania w znakach na minutę oraz słowach na minutę.

In [ ]:
from datetime import timedelta

key_events = []

def report_key(event):
    # Pobieramy aktualny czas
    timestamp = datetime.now()
    # Zapisujemy czas i wciśnięty klawisz do listy
    key_events.append((timestamp, event.name))

# Ustawienie callbacka dla zdarzeń klawiatury
keyboard.on_release(callback=report_key)

def calculate_typing_speed():
    if not key_events:
        return "No key events recorded."

    total_time = timedelta()
    total_chars = 0
    total_words = 0
    prev_time = key_events[0][0]

    for i in range(1, len(key_events)):
        current_time = key_events[i][0]
        key = key_events[i][1]

        # Obliczamy czas między kolejnymi naciśnięciami klawiszy
        time_diff = current_time - prev_time

        # Jeśli różnica czasu jest mniejsza niż 5 sekund, dodajemy do całkowitego czasu
        if time_diff <= timedelta(seconds=5):
            total_time += time_diff
            total_chars += 1
            if key == "space":
                total_words += 1

        prev_time = current_time

    # Dodajemy ostatnie słowo (bo nie zawsze kończy się spacją)
    total_words += 1

    # Obliczamy prędkość pisania
    total_minutes = total_time.total_seconds() / 60
    chars_per_minute = total_chars / total_minutes if total_minutes > 0 else 0
    words_per_minute = total_words / total_minutes if total_minutes > 0 else 0

    return f"Typing Speed: {chars_per_minute:.2f} chars/min, {words_per_minute:.2f} words/min"

# Uruchomienie keyloggera i czekanie na zdarzenia klawiatury
keyboard.wait()

# Po zakończeniu pisania, wyliczamy prędkość pisania
print(calculate_typing_speed())

Wróćmy teraz do procesu tłumaczenia. Analiza uderzeń klawiszy wykonanych podczas tłumaczenia pozwala wykryć dłuższe pauzy. Pauzy te najczęściej wskazują miejsca, w których tłumacz musi się głębiej zastanowić nad tłumaczeniem danego słowa lub frazy. Przerwę tę wykorzystuje na przykład na sprawdzenie tłumaczenia lub definicji w słowniku, przeglądanie wyników z pamięci tłumaczeń lub korzystanie z innych pomocy (eye-tracking mógłby w tym przypadku rozstrzygnąć, czym w istocie zajmuje się w tym momencie tłuamcz). Jest też możliwe, że tłumacz poświęca pauzę na tzw. cognitive pause-and-unload - rodzaj zamyślenia, pozwalający oczyścić myśli. Z punktu widzenia projektowania systemu wspomagającego tłumaczenie niezwykle istotna jest informacja, nad czym tłumacz musi się dłużej zastanowić. Minimalizacja liczby i czasu trwania takich przerw jest szansą na usprawnienie procesu tłumaczenia.

### Ćwiczenie 3: Napisz program do wykrywania przerw w pisaniu. Raportuj długość oraz miejsce wystąpienia przerwy podając 20-znakowy kontekst z każdej strony. Wykryj każdą przerwę dłuższą niż 3 sekundy, posortuj wyniki malejąco po długości przerwy.

In [ ]:
key_events = []

def report_key(event):
    # Pobieramy aktualny czas
    timestamp = datetime.now()
    # Zapisujemy czas i wciśnięty klawisz do listy
    key_events.append((timestamp, event.name))

# Ustawienie callbacka dla zdarzeń klawiatury
keyboard.on_release(callback=report_key)

def find_pauses():
    if not key_events:
        return "No key events recorded."

    pauses = []
    prev_time = key_events[0][0]
    full_text = ''.join([key[1] if key[1] != "space" else " " for key in key_events])

    for i in range(1, len(key_events)):
        current_time = key_events[i][0]
        key = key_events[i][1]

        # Obliczamy czas między kolejnymi naciśnięciami klawiszy
        time_diff = current_time - prev_time

        # Jeśli różnica czasu jest większa niż 3 sekundy, zapisujemy przerwę
        if time_diff > timedelta(seconds=3):
            start_idx = max(0, i - 21)
            end_idx = min(len(full_text), i + 20)
            context = full_text[start_idx:end_idx]
            pauses.append((time_diff.total_seconds(), context))

        prev_time = current_time

    # Sortowanie przerw malejąco po długości
    pauses.sort(reverse=True, key=lambda x: x[0])

    return pauses

# Uruchomienie keyloggera i czekanie na zdarzenia klawiatury
keyboard.wait()

# Po zakończeniu pisania, wykrywamy przerwy
pauses = find_pauses()

# Wyświetlanie przerw
for pause in pauses:
    length, context = pause
    print(f"Pause length: {length:.2f} seconds, Context: '{context}'")
